# CodeSearchNet Data Source Notice

In [ ]:
!mkdir /content/CodeSearchNet

mkdir: cannot create directory ‘/content/CodeSearchNet’: File exists


In [ ]:
%%capture
!pip install docopt

After the CodeSearchNet dataset was archieved, the S3 bucket was taken offline. As a result, following the installation on the github installation guide will not work. A short illustration can be seen down below.

In [ ]:
import os
from subprocess import call, check_call, CalledProcessError

destination_dir = "/content/CodeSearchNet"

if not os.path.exists(destination_dir):
    os.makedirs(destination_dir)
os.chdir(destination_dir)

try:
    language = "python"
    check_call(['wget', f'https://s3.amazonaws.com/code-search-net/CodeSearchNet/v2/{language}.zip', '-O', f'{language}.zip'])
    check_call(['unzip', f'{language}.zip'])
    check_call(['rm', f'{language}.zip'])
except CalledProcessError as e:
    print(f"Error: {e}")
    print(f"Error executing command {e.cmd}")
    print(f"Returned code {e.returncode}")

Error: Command '['wget', 'https://s3.amazonaws.com/code-search-net/CodeSearchNet/v2/python.zip', '-O', 'python.zip']' returned non-zero exit status 8.
Error executing command ['wget', 'https://s3.amazonaws.com/code-search-net/CodeSearchNet/v2/python.zip', '-O', 'python.zip']
Returned code 8


Instead, we download the dataset from Hugging Face. Updating `datasets` might not be necessary but might sometimes be helpful to avoid errors concering caching in the local file system

# Data Fetching

In [1]:
%%capture

!pip install datasets==3.6.0

In [2]:
!pip show datasets

Name: datasets
Version: 3.6.0
Summary: HuggingFace community-driven open-source library of datasets
Home-page: https://github.com/huggingface/datasets
Author: HuggingFace Inc.
Author-email: thomas@huggingface.co
License: Apache 2.0
Location: /usr/local/lib/python3.11/dist-packages
Requires: dill, filelock, fsspec, huggingface-hub, multiprocess, numpy, packaging, pandas, pyarrow, pyyaml, requests, tqdm, xxhash
Required-by: torchtune


Make sure to restart the runtime to allow the changes to take effect

In [1]:
from datasets import load_dataset

# Load the dataset
dataset = load_dataset("code_search_net", "python")
# dataset = load_dataset("Nan-Do/code-search-net-python")

train_data = dataset["train"]
test_data = dataset["test"]

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md: 0.00B [00:00, ?B/s]

code_search_net.py: 0.00B [00:00, ?B/s]

The repository for code_search_net contains custom code which must be executed to correctly load the dataset. You can inspect the repository content at https://hf.co/datasets/code_search_net.
You can avoid this prompt in future by passing the argument `trust_remote_code=True`.

Do you wish to run the custom code? [y/N] y


python.zip:   0%|          | 0.00/941M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/412178 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/22176 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/23107 [00:00<?, ? examples/s]

We can inspect the contents of the dataset object for the training, testing, and validation datasets.

In [2]:
print(train_data.features.keys())

dict_keys(['repository_name', 'func_path_in_repository', 'func_name', 'whole_func_string', 'language', 'func_code_string', 'func_code_tokens', 'func_documentation_string', 'func_documentation_tokens', 'split_name', 'func_code_url'])


In [3]:
train_data.shape

(1880853, 11)

# Question Generation Pipeline

In [4]:
import itertools
import torch
from transformers import (
    AutoModelForSeq2SeqLM,
    AutoTokenizer,
    PreTrainedModel,
    PreTrainedTokenizer
)
from nltk import sent_tokenize

from typing import (
    Tuple,
    Dict,
    Literal,
    List,
    Any,
    Generator,
    overload,
    Union
)

class QGPipeline:
    def __init__(
        self,
        model: str,
        qg_format: Literal["highlight"] = "highlight",
        exclude_after: List[str] = [],
        use_cuda: bool = False
    ):

        self.model = AutoModelForSeq2SeqLM.from_pretrained(model)
        self.tokenizer = AutoTokenizer.from_pretrained(model)
        self.qg_format = qg_format

        assert self.model.__class__.__name__ == "T5ForConditionalGeneration"

        self.device = torch.device("cuda" if torch.cuda.is_available() and use_cuda else "cpu")
        self.model.to(self.device)
        self.model.eval()
        self.use_cuda = use_cuda
        self._exclude_after = exclude_after
        print(f"Using {self.device}")

    def __call__(self, input: Union[Tuple[str, str], List[Tuple[str, str]]]):
        if isinstance(input, tuple):
            # Handle single input
            func_name, docstring = input
            questions = self._generate_questions(func_name, docstring)
            output = [{'answer': func_name, 'question': que} for que in questions]
            if output:
                 return output[0]
            else:
                 return {}

        elif isinstance(input, list) and all(isinstance(item, tuple) for item in input):
            # Handle batch input with proper error handling
            return self._process_batch_generator(input)
        else:
            raise TypeError("Invalid input type. Expected a tuple (func_name, docstring) or a list of such tuples.")


    def _process_batch_generator(self, batch_input: List[Tuple[str, str]]) -> Generator[Dict[str, Any], None, None]:
        """
        Process batch input and yield results with error handling per item
        """
        for i, (func_name, docstring) in enumerate(batch_input):
            try:
                questions = self._generate_questions(func_name, docstring)
                output = [{'answer': func_name, 'question': que} for que in questions]

                if output:
                    yield {
                        'success': True,
                        'index': i,
                        'function_name': func_name,
                        'docstring': docstring,
                        'model_output': output[0],
                        'error': None
                    }
                else:
                    yield {
                        'success': False,
                        'index': i,
                        'function_name': func_name,
                        'docstring': docstring,
                        'model_output': {},
                        'error': 'No questions generated'
                    }

            except Exception as e:
                yield {
                    'success': False,
                    'index': i,
                    'function_name': func_name,
                    'docstring': docstring,
                    'model_output': {},
                    'error': str(e)
                }

    def _generate_questions(self, func_name, docstring):
        #TODO: This can be re-written in a more forceful way for the llm
        inputs = self._prepare_inputs_for_question_extraction(func_name, docstring)

        inputs = self._tokenize(inputs, padding=True, truncation=True)

        with torch.no_grad():
            outs = self.model.generate(
                input_ids=inputs['input_ids'].to(self.device),
                attention_mask=inputs['attention_mask'].to(self.device),
                num_beams=4,

                max_length=32
            )

        questions = [self.tokenizer.decode(ids, skip_special_tokens=True) for ids in outs]

        return questions

    def _tokenize(self, inputs, padding=True, truncation=True, add_special_tokens=True, max_length=512):
        tokenized_inputs = self.tokenizer(
            inputs,
            max_length=max_length,
            add_special_tokens=add_special_tokens,
            truncation=truncation,
            padding=padding,
            return_tensors="pt"
        )
        return tokenized_inputs

    def _prepare_inputs_for_question_extraction(self, func_name, docstring):
        #NOTE: experimental, consider removing :params and :return values
        #manual observation suggests the model struggles to understand the pupose of the function in their presense
        for string in self._exclude_after:
            param_idx = docstring.find(string)
            if param_idx != -1:
                docstring = docstring[:param_idx]
            docstring = docstring.strip()
        input = f"answer: <hl>The function is {func_name}<hl>. Context: {docstring} </s>"

        return [input]

    @property
    def exclude_after(self):
        return self._exclude_after

    @exclude_after.setter
    def exclude_after(self, value):
        self._exclude_after = value

In [5]:
finetuned_t5 = QGPipeline(model="valhalla/t5-base-qg-hl")

config.json: 0.00B [00:00, ?B/s]

pytorch_model.bin:   0%|          | 0.00/892M [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/892M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/129 [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

added_tokens.json:   0%|          | 0.00/15.0 [00:00<?, ?B/s]

special_tokens_map.json: 0.00B [00:00, ?B/s]

You are using the default legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This is expected, and simply means that the `legacy` (previous) behavior will be used so nothing changes for you. If you want to use the new behaviour, set `legacy=False`. This should only be set if you understand what it means, and thoroughly read the reason why this was added as explained in https://github.com/huggingface/transformers/pull/24565


Using cpu


In [6]:
func_name = train_data[4]['func_name']
docstring = train_data[4]['func_documentation_string']
print(docstring)
finetuned_t5((func_name, docstring))

:return: ids of test reports


{'answer': 'ReportsTable.get_report_list',
 'question': 'What is the name of the function that returns the ids of test reports?'}

The result looks promising. Let's run the model for the first 20 doc strings in our dataset

In [ ]:
for i in range(10):
    func_name = train_data[i]['func_name']
    p = docstring = train_data[i]['func_documentation_string']
    print(f"========Sample{i+1}==========")
    idx = docstring.find(":param")
    if idx != -1:
        p = docstring[:idx]
    p = docstring[:].strip()
    print(f"Docstring: {docstring}")
    print(finetuned_t5((func_name, docstring)))


========Sample1==========
Docstring: update db entry

        :param field_dict: dictionary of fields and values
        :param where_clause: where clause for the update
{'answer': 'Table.update', 'question': 'What is the function for Table.update?'}
========Sample2==========
Docstring: insert new db entry

        :param fields: list of fields to insert
        :param values: list of values to insert
        :return: row id of the new row
{'answer': 'Table.insert', 'question': 'What is the name of the function that inserts a new db entry?'}
========Sample3==========
Docstring: :param report: the report to store
        :param test_id: the id of the test reported
        :return: report id
{'answer': 'ReportsTable.store', 'question': 'What is the name of the function that stores the report?'}
========Sample4==========
Docstring: get report by the test id

        :param test_id: test id
        :return: Report object
{'answer': 'ReportsTable.get', 'question': 'What is the name of the f

In [ ]:
zipped5 = zip(train_data[:5]['func_name'], train_data[:5]['func_documentation_string'])

generator = finetuned_t5(list(zipped5))
print(generator)

for item in generator:
    ans, ques = item['function_name'], item['model_output']['question']
    print(f"========Sample==========")
    print(f"Question: {ques}")
    print(f"Answer: {ans}")
    print()

<generator object QGPipeline._process_batch_generator at 0x7833286165c0>
========Sample==========
Question: What is the function that ensures that the WebSocket connection is open?
Answer: WebSocketCommonProtocol.ensure_open

========Sample==========
Question: What is the function that reads incoming messages and puts them in a queue?
Answer: WebSocketCommonProtocol.transfer_data

========Sample==========
Question: What is the function that reads a single message from the connection?
Answer: WebSocketCommonProtocol.read_message

========Sample==========
Question: What is the function that reads a single data frame from a connection?
Answer: WebSocketCommonProtocol.read_data_frame

========Sample==========
Question: What is the function that reads a single frame from a connection?
Answer: WebSocketCommonProtocol.read_frame



# Dataset Processor

In [ ]:
import json
import pandas as pd
from pathlib import Path
from tqdm import tqdm
import time
from typing import List, Tuple, Dict, Any
from datasets import Dataset, DatasetDict
from huggingface_hub import repo_exists, auth_check
from huggingface_hub.utils import GatedRepoError, RepositoryNotFoundError


def dataset_exists(dataset_name, token=None):
    try:
        load_dataset(dataset_name, token=token, streaming=True)
        return True
    except (RepositoryNotFoundError, OSError, ValueError):
        return False


class DocstringDatasetProcessor:
    def __init__(
        self,
        hf_dataset_name: str,
        batch_size: int = 1000,
        token: str = "",
        save_locally: bool = False,
        local_cache_dir: str = "./cache",
        private_repo: bool = False,
    ):

        self.hf_dataset_name = hf_dataset_name
        self.batch_size = batch_size
        self.private_repo = private_repo
        self.local_cache_dir = Path(local_cache_dir)
        self.local_cache_dir.mkdir(exist_ok=True)
        self.save_locally = save_locally

        self.processed_count = 0
        self.failed_count = 0
        self.all_generated_data = []

        self.token = token

    def process_batch(
        self, batch_data: List[Tuple[str, str]], pipeline: QGPipeline, batch_id: int
    ) -> List[Dict[str, Any]]:
        """Process a batch of (func_name, docstring) tuples with individual error handling"""
        batch_results = []
        batch_success_count = 0
        batch_failure_count = 0

        print(batch_data)

        # Process the entire batch through pipeline
        try:
            generator = pipeline(batch_data)
            for result in generator:

                if result["success"]:
                    batch_results.append(
                        {
                            "function_name": result["function_name"],
                            "docstring": result["docstring"],
                            "question": result["model_output"]["question"],
                        }
                    )
                    batch_success_count += 1
                else:
                    print(
                        f"Failed to process {result['function_name']}: {result['error']}"
                    )
                    batch_failure_count += 1

        except Exception as e:
            # Catastrophic failure - entire batch failed
            print(f"Catastrophic batch failure {batch_id}: {e}")
            batch_failure_count = len(batch_data)
            batch_success_count = 0

        self.processed_count += batch_success_count
        self.failed_count += batch_failure_count

        print(
            f"Batch {batch_id}: {batch_success_count} successful, "
            f"{batch_failure_count} failed out of {len(batch_data)} items"
        )

        if self.save_locally and batch_results:
            self._save_batch_locally(batch_results, batch_id)

        return batch_results

    def _save_batch_locally(self, batch_results: List[Dict], batch_id: int):
        batch_file = self.local_cache_dir / f"batch_{batch_id}.jsonl"
        with open(batch_file, "w") as f:
            for item in batch_results:
                json.dump(item, f)
                f.write("\n")

    def process_full_dataset(self, dataset, pipeline, start_idx: int = 0):
        """Process the entire data set and upload to hugging face"""

        if not self.token:
            print("Hugging face token not provided. Terminatng")
            return

        if not self._can_upload():
            print("Cannot upload to Hugging Face: insufficient permissions or repo access.")
            return

        print(f"Starting processing of {len(dataset)} items from index {start_idx}")

        start_time = time.time()

        for batch_start in tqdm(
            range(start_idx, len(dataset), self.batch_size), desc="Processing batches"
        ):
            batch_end = min(batch_start + self.batch_size, len(dataset))
            batch_data = dataset[batch_start:batch_end]
            batch_id = batch_start // self.batch_size

            batch_results = self.process_batch(batch_data, pipeline, batch_id)
            self.all_generated_data.extend(batch_results)

            # print progress
            if batch_id % 10 == 0:
                elapsed = time.time() - start_time
                rate = self.processed_count / elapsed if elapsed > 0 else 0
                print(
                    f"Processed {self.processed_count} items in {elapsed:.2f} seconds. Rate: {rate:.2f} items/sec"
                )

            # final statistics
            total_time = time.time() - start_time
            print(
                f"Processed {self.processed_count} items in {total_time:.2f} seconds. Rate: {self.processed_count / total_time:.2f} items/sec"
            )

            self._upload_to_hf()


    def _can_upload(self):
        namespace = self.hf_dataset_name.split('/')[0]
        try:
            if dataset_exists(self.hf_dataset_name):
                return True
            else:
                from huggingface_hub import whoami
                user_info = whoami(token=self.token)
                if namespace == user_info["name"]:
                    return True
                else:
                    return False
        except Exception as e:
            print(e)
            return False

    def _upload_to_hf(self):
        try:
            new_dataset = Dataset.from_list(self.all_generated_data)
            new_dataset = new_dataset.map(
                lambda x: {
                    **x,
                    "id": f"{x['function_name']}_{hash(x['docstring']) % 10000}",
                }
            )

            if dataset_exists(self.hf_dataset_name):
                try:
                    existing_dataset_dict = load_dataset(self.hf_dataset_name, token=self.token)
                    if "train" in existing_dataset_dict:
                        existing_dataset = existing_dataset_dict["train"]
                        combined_data = existing_dataset.to_list() + new_dataset.to_list()
                        seen_ids = set()
                        merged_data = []
                        for item in combined_data:
                            if item["id"] not in seen_ids:
                                merged_data.append(item)
                                seen_ids.add(item["id"])
                        merged_dataset = Dataset.from_list(merged_data)
                        dataset_dict = DatasetDict({"train": merged_dataset})
                    else:
                        dataset_dict = DatasetDict({"train": new_dataset})
                except Exception as e:
                    print(f"Error loading existing dataset, proceeding with new data only: {e}")
                    dataset_dict = DatasetDict({"train": new_dataset})
            else:
                dataset_dict = DatasetDict({"train": new_dataset})

            print("Uploading dataset to Hugging Face...")

            dataset_dict.push_to_hub(
                self.hf_dataset_name,
                token=self.token,
                private=self.private_repo,
                commit_message=f"Add {len(self.all_generated_data)} docstring-question pairs",
            )

            print(
                f"Successfully uploaded dataset to https://huggingface.co/datasets/{self.hf_dataset_name}"
            )

        except Exception as e:
            print(f"Error uploading to Hugging Face: {e}")
            if self.save_locally:
                print("Data is available locally in cached directory")
            raise

    def load_from_hf(self):
        """Load the dataset from Hugging Face"""
        try:
            dataset = load_dataset(self.hf_dataset_name, token=self.token)
            print(f"Successfully loaded dataset from {self.hf_dataset_name}")
            return dataset
        except Exception as e:
            print(f"Error loading dataset from Hugging Face: {e}")
            raise

    # TODO: resume processing from local cache file
    # TODO: upload from colab cache to permanent file location (local or drive)


In [12]:
# Constants

from google.colab import userdata

HUGGING_FACE_TOKEN = userdata.get("HUGGING_FACE_TOKEN")
hf_dataset_name = "mrinjera/testing"

In [ ]:
dataset_processor = DocstringDatasetProcessor(hf_dataset_name, batch_size=10, token=HUGGING_FACE_TOKEN)

batch_raw_data = zip(train_data[:500]['func_name'], train_data[:500]['func_documentation_string'])
batch_zip_data = list(batch_raw_data)

pipeline = finetuned_t5
dataset_processor.process_full_dataset(batch_zip_data, pipeline)

README.md:   0%|          | 0.00/378 [00:00<?, ?B/s]

Starting processing of 500 items from index 0


Processing batches:   0%|          | 0/50 [00:00<?, ?it/s]

[('Utility.findArgs', 'Extracts the list of arguments that start with any of the specified prefix values'), ('Utility.stripArgs', 'Removes any arguments in the supplied list that are contained in the specified blacklist'), ('Utility.capture', 'Executes a child process and captures its output'), ('Utility.run', 'Executes a child process and waits for it to complete'), ('UnrealManagerBase.setEngineRootOverride', 'Sets a user-specified directory as the root engine directory, overriding any auto-detection'), ('UnrealManagerBase.getEngineRoot', 'Returns the root directory location of the latest installed version of UE4'), ('UnrealManagerBase.getEngineVersion', 'Returns the version number of the latest installed version of UE4'), ('UnrealManagerBase.getEngineChangelist', 'Returns the compatible Perforce changelist identifier for the latest installed version of UE4'), ('UnrealManagerBase.isInstalledBuild', 'Determines if the Engine is an Installed Build'), ('UnrealManagerBase.getEditorBinary'

Map:   0%|          | 0/10 [00:00<?, ? examples/s]

...

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Uploading...:   0%|          | 0.00/96.0k [00:00<?, ?B/s]

Processing batches: 100%|██████████| 50/50 [27:25<00:00, 32.90s/it]

Successfully uploaded dataset to https://huggingface.co/datasets/mrinjera/testing


In [ ]:
for i in range(10):
    print(train_data[i]['func_documentation_string'])

Check that the WebSocket connection is open.

        Raise :exc:`~websockets.exceptions.ConnectionClosed` if it isn't.
Read incoming messages and put them in a queue.

        This coroutine runs in a task until the closing handshake is started.
Read a single message from the connection.

        Re-assemble data frames if the message is fragmented.

        Return ``None`` when the closing handshake is started.
Read a single data frame from the connection.

        Process control frames received before the next data frame.

        Return ``None`` if a close frame is encountered before any data frame.
Read a single frame from the connection.
Write a close frame if and only if the connection state is OPEN.

        This dedicated coroutine must be used for writing close frames to
        ensure that at most one close frame is sent on a given connection.
Send a Ping frame and wait for a Pong frame at regular intervals.

        This coroutine exits when the connection terminates and o

# Localized Dataset processor

In [30]:
import json
from pathlib import Path
from tqdm import tqdm
import time
from typing import List, Tuple, Dict
from datasets import Dataset, DatasetDict
from huggingface_hub.errors import RepositoryNotFoundError
from datasets import load_dataset

def dataset_exists(dataset_name, token=None):
    try:
        load_dataset(dataset_name, token=token, streaming=True)
        return True
    except (RepositoryNotFoundError, OSError, ValueError):
        return False


class DocstringDatasetProcessor:
    def __init__(
        self,
        hf_dataset_name: str,
        batch_size: int = 1000,
        token: str = "",
        local_cache_dir: str = "./cache",
        private_repo: bool = False,
    ):

        self.hf_dataset_name = hf_dataset_name
        self.batch_size = batch_size
        self.private_repo = private_repo
        self.local_cache_dir = Path(local_cache_dir)
        self.local_cache_dir.mkdir(exist_ok=True)

        self.processed_count = 0
        self.failed_count = 0

        self.token = token

        self.mounted_dataset_dict = DatasetDict()

    def process_batch(
        self, batch_data: List[Tuple[str, str]], pipeline: QGPipeline, batch_id: int, split: str = ""
    ):
        """Process a batch of (func_name, docstring) tuples. Results are saved locally; uploading is handled separately after all batches are processed."""
        batch_results = []
        batch_success_count = 0
        batch_failure_count = 0

        try:
            generator = pipeline(batch_data)
            for result in generator:
                if isinstance(result, dict):
                    if result["success"]:
                        #TODO: consider reducing memory overhead as batch docstring exists in two places
                        batch_results.append(
                            {
                                "function_name": result["function_name"],
                                "docstring": result["docstring"],
                                "question": result["model_output"]["question"],
                            }
                        )
                        batch_success_count += 1
                    else:
                        print(
                            f"Failed to process {result['function_name']}: {result['error']}"
                        )
                        batch_failure_count += 1

        except Exception as e:
            # entire batch failed
            print(f"Catastrophic batch failure {batch_id}: {e}")
            batch_failure_count = len(batch_data)
            batch_success_count = 0

        self.processed_count += batch_success_count
        self.failed_count += batch_failure_count

        print(
            f"Batch {batch_id}: {batch_success_count} successful, "
            f"{batch_failure_count} failed out of {len(batch_data)} items"
        )

        if batch_results:
            self._save_batch_locally(batch_results, batch_id, split=split)

    def _save_batch_locally(self, batch_results: List[Dict], batch_id: int, split: str = ""):
        if split:
            split_dir = self.local_cache_dir / split
            split_dir.mkdir(parents=True, exist_ok=True)
            batch_file = split_dir / f"batch_{batch_id}.jsonl"
        else:
            batch_file = self.local_cache_dir / f"batch_{batch_id}.jsonl"
        with open(batch_file, "w") as f:
            for item in batch_results:
                json.dump(item, f)
                f.write("\n")

    def process_full_dataset(self, dataset, pipeline: QGPipeline, start_idx: int = 0, split: str = ""):
        """Process the entire data set and store all processed batches locally."""

        if not self.token:
            print("Hugging face token not provided. Terminating")
            return

        print(f"Starting processing of {len(dataset)} items from index {start_idx}")

        start_time = time.time()

        for batch_start in tqdm(
            range(start_idx, len(dataset), self.batch_size), desc="Processing batches"
        ):
            batch_end = min(batch_start + self.batch_size, len(dataset))
            batch_data = dataset[batch_start:batch_end]
            batch_id = batch_start // self.batch_size

            self.process_batch(batch_data, pipeline, batch_id, split=split)

        total_time = time.time() - start_time
        print(
            f"Processed {self.processed_count} items in {total_time:.2f} seconds. Rate: {self.processed_count / total_time:.2f} items/sec"
        )

        print("All batches processed and stored locally.")


    def _can_upload(self):
        namespace = self.hf_dataset_name.split('/')[0]
        try:
            if dataset_exists(self.hf_dataset_name):
                return True
            else:
                from huggingface_hub import whoami
                user_info = whoami(token=self.token)
                if namespace == user_info["name"]:
                    return True
                else:
                    return False
        except Exception as e:
            print(e)
            return False

    def mount_for_upload(self, directory_path: str, *, split: str):
        """Perepares locally processed data to upload"""
        import glob
        import os

        local_data = []
        batch_files = sorted(glob.glob(os.path.join(directory_path, "batch_*.jsonl")))
        for batch_file in batch_files:
            with open(batch_file, "r") as f:
                for line in f:
                    item = json.loads(line)
                    local_data.append(item)

        local_dataset = Dataset.from_list(local_data)
        self.mounted_dataset_dict[split] = local_dataset

    def upload_local_to_hf(self, hf_dataset_name, private_repo=False):

        dataset_dict = self.mounted_dataset_dict
        token = self.token
        print("Uploading dataset to Hugging Face...")

        dataset_dict.push_to_hub(
            hf_dataset_name,
            token=token,
            private=private_repo,
            commit_message=f"Added {str(dataset_dict.num_rows)}"
        )

        print(
            f"Successfully uploaded dataset to https://huggingface.co/datasets/{hf_dataset_name}"
        )

    def load_from_hf(self):
        """Load the dataset from Hugging Face"""
        try:
            dataset = load_dataset(self.hf_dataset_name, token=self.token)
            print(f"Successfully loaded dataset from {self.hf_dataset_name}")
            return dataset
        except Exception as e:
            print(f"Error loading dataset from Hugging Face: {e}")
            raise

    # TODO: resume processing from local cache file
    # TODO: upload from colab cache to permanent file location (local or drive)


In [31]:
dataset_processor = DocstringDatasetProcessor(hf_dataset_name, batch_size=10, token=HUGGING_FACE_TOKEN)

batch_raw_data = zip(train_data[:5]['func_name'], train_data[:5]['func_documentation_string'])
batch_zip_data = list(batch_raw_data)

pipeline = finetuned_t5
dataset_processor.process_full_dataset(batch_zip_data, pipeline, split="train")

Starting processing of 5 items from index 0


Processing batches: 100%|██████████| 1/1 [00:17<00:00, 17.68s/it]

Batch 0: 5 successful, 0 failed out of 5 items
Processed 5 items in 17.68 seconds. Rate: 0.28 items/sec
All batches processed and stored locally.


In [32]:
test_batch_raw_data = zip(test_data[:5]['func_name'], test_data[:5]['func_documentation_string'])
test_batch_zip_data = list(test_batch_raw_data)

dataset_processor.process_full_dataset(test_batch_zip_data, pipeline, split="test")

Starting processing of 5 items from index 0


Processing batches: 100%|██████████| 1/1 [00:13<00:00, 13.94s/it]

Batch 0: 5 successful, 0 failed out of 5 items
Processed 10 items in 13.95 seconds. Rate: 0.72 items/sec
All batches processed and stored locally.


In [33]:
dataset_processor.mount_for_upload("cache/test", split="test")
dataset_processor.mount_for_upload("cache/train", split="train")

In [34]:
dataset_processor.upload_local_to_hf("mrinjera/testing2")

Uploading dataset to Hugging Face...


Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Uploading...:   0%|          | 0.00/2.29k [00:00<?, ?B/s]

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Uploading...:   0%|          | 0.00/2.63k [00:00<?, ?B/s]

README.md:   0%|          | 0.00/374 [00:00<?, ?B/s]

Successfully uploaded dataset to https://huggingface.co/datasets/mrinjera/testing2


In [25]:
dataset_processor.upload_local_to_hf("cache/train", "mrinjera/testing2", HUGGING_FACE_TOKEN, "test")

Uploading dataset to Hugging Face...


Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/1 [00:00<?, ?ba/s]

Uploading...:   0%|          | 0.00/3.09k [00:00<?, ?B/s]

README.md:   0%|          | 0.00/225 [00:00<?, ?B/s]

Successfully uploaded dataset to https://huggingface.co/datasets/mrinjera/testing2


# Model Training

In [26]:
import torch
import pandas as pd
from datasets import Dataset, load_dataset
from torch.utils.data import DataLoader
from sklearn.model_selection import train_test_split
from typing import List, Dict, Tuple
from sentence_transformers.evaluation import InformationRetrievalEvaluator
from sentence_transformers.training_args import BatchSamplers
from sentence_transformers import (
    models,
    SentenceTransformer,
    SentenceTransformerModelCardData,
    SentenceTransformerTrainer,
    SentenceTransformerTrainingArguments,
    InputExample,
    losses,
)
from transformers import EarlyStoppingCallback
from peft import LoraConfig, TaskType

DATASET_NAME = "mrinjera/testing"
MODEL_NAME = "microsoft/codebert-base"
OUTPUT_MODEL_PATH = "./sbert-function-retrieval"
BATCH_SIZE = 16
EPOCHS = 4
LEARNING_RATE = 2e-5
WARMUP_STEPS = 1000
EVALUATION_STEPS = 5000


def load_and_process_dataset(
    dataset_name: str, token: str
) -> Tuple[pd.DataFrame, pd.DataFrame]:
    """Load the dataset and process it for training."""
    print(f"Loading dataset: {dataset_name}")

    dataset = load_dataset(dataset_name, token=token)

    train_df = pd.DataFrame(dataset["train"])
    test_df = pd.DataFrame(dataset["test"])

    print(f"Train dataset loaded with {len(train_df)} examples")
    print(f"Test dataset loaded with {len(test_df)} examples")
    print(f"Dataset columns: {train_df.columns.tolist()}")

    train_df = train_df.dropna(subset=["docstring", "question"])
    test_df = test_df.dropna(subset=["docstring", "question"])

    print(f"  Train: {len(train_df)} examples")
    print(f"  Test: {len(test_df)} examples")

    return train_df, test_df


# NOTE: This is not being used in the current implementation
def create_training_examples(df: pd.DataFrame) -> List[InputExample]:
    """Create InputExample objects for SBERT training."""
    examples = []

    for idx, row in df.iterrows():
        # input example with question as query and func_name + docstring as positive document
        combined_text = f"{row['function_name']} {row['docstring']}"
        example = InputExample(texts=[str(row["question"]), combined_text], label=1.0)
        examples.append(example)

    print(f"Created {len(examples)} training examples")
    return examples


def create_evaluation_data(
    eval_df: pd.DataFrame,
) -> Tuple[Dict[str, str], Dict[str, str], Dict[str, set]]:
    """Create evaluation data for Information Retrieval evaluation."""
    # Split data for evaluation
    # eval_df = df.sample(n=min(1000, len(df) // 10), random_state=42)

    queries = {}
    corpus = {}
    relevant_docs = {}

    for idx, row in eval_df.iterrows():
        query_id = f"q_{idx}"
        doc_id = f"d_{idx}"

        queries[query_id] = row["question"]
        corpus[doc_id] = f"{row['function_name']} {row['docstring']}"
        relevant_docs[query_id] = doc_id

    print(
        f"Created evaluation data with {len(queries)} queries and {len(corpus)} documents"
    )
    return queries, corpus, relevant_docs


def create_validation_split(
    train_df: pd.DataFrame, validation_size: float = 0.1
) -> Tuple[pd.DataFrame, pd.DataFrame]:
    """Create a validation split from training data for monitoring during training."""
    train_split, val_split = train_test_split(
        train_df, test_size=validation_size, random_state=42, stratify=None
    )

    print("Created validation split:")
    print(f"  Training: {len(train_split)} examples")
    print(f"  Validation: {len(val_split)} examples")

    return train_split, val_split


def evaluate_on_test_set(
    model: SentenceTransformer,
    test_queries: Dict[str, str],
    test_corpus: Dict[str, str],
    test_relevant_docs: Dict[str, set],
) -> Dict[str, float]:
    """Evaluate the trained model on the test set."""
    print("Evaluating model on test set...")

    # Create test evaluator
    test_evaluator = InformationRetrievalEvaluator(
        queries=test_queries,
        corpus=test_corpus,
        relevant_docs=test_relevant_docs,
        name="test-eval",
    )

    # Evaluate
    test_score = test_evaluator(model, output_path=OUTPUT_MODEL_PATH + "/test_results")

    print(f"Test evaluation completed. Score: {test_score}")
    return test_score


def initialize_model(model_name: str) -> SentenceTransformer:
    transformer = models.Transformer(MODEL_NAME)
    pooling = models.Pooling(
        transformer.get_word_embedding_dimension(), pooling_mode="max"
    )
    model = SentenceTransformer(
        modules=[transformer, pooling],
        model_card_data=SentenceTransformerModelCardData(
            language="en",
            license="apache-2.0",
            model_name=f"{model_name} adapter finetuned on CodeSearchNet question-docstring pairs",
        ),
    )
    return model


def train_model(
    model: SentenceTransformer,
    train_dataset: Dataset,
    val_queries: Dict[str, str],
    val_corpus: Dict[str, str],
    val_relevant_docs: Dict[str, set],
    device: torch.device,
) -> SentenceTransformer:
    """Train the SBERT model with Multiple Negatives Ranking Loss."""

    if isinstance(train_dataset, pd.DataFrame):
        train_dataset = Dataset.from_pandas(train_dataset)


    peft_config = LoraConfig(
        task_type=TaskType.FEATURE_EXTRACTION,
        inference_mode=False,
        r=64,
        lora_alpha=128,
        lora_dropout=0.1,
    )

    model.add_adapter(peft_config, adapter_name="This will never exist")

    loss = losses.MultipleNegativesRankingLoss(model)

    # TODO: consider including epochs, warmup steps, optimizer
    args = SentenceTransformerTrainingArguments(
        output_dir=OUTPUT_MODEL_PATH + "/training_checkpoints/",
        # Optional training parameters:
        num_train_epochs=1,
        per_device_train_batch_size=1024,
        per_device_eval_batch_size=1024,
        learning_rate=2e-5,
        warmup_ratio=0.1,
        fp16=False,  # Set to False if you get an error that your GPU can't run on FP16
        bf16=False,  # Set to True if you have a GPU that supports BF16
        batch_sampler=BatchSamplers.NO_DUPLICATES,  # MultipleNegativesRankingLoss benefits from no duplicate samples in a batch
        # Optional tracking/debugging parameters:
        eval_strategy="steps",
        eval_steps=100,
        save_strategy="steps",
        save_steps=100,
        save_total_limit=2,
        logging_steps=25,
        logging_first_step=True,
        load_best_model_at_end=True,
        metric_for_best_model="eval_val_cosine",
        # run_name=run_name,  # Will be used in W&B if `wandb` is installed
    )

    evaluator = InformationRetrievalEvaluator(
        queries=val_queries,
        corpus=val_corpus,
        relevant_docs=val_relevant_docs,
        name="CodeSearchNet retrieval evaluator",
    )

    early_stopping = EarlyStoppingCallback(
        early_stopping_patience=3, early_stopping_threshold=0.01
    )

    trainer = SentenceTransformerTrainer(
        model=model,
        args=args,
        train_dataset=train_dataset,
        loss=loss,
        evaluator=evaluator,
        callbacks=[early_stopping],
    )

    trainer.train()

    model.save_pretrained(OUTPUT_MODEL_PATH)

    return model

In [15]:
from google.colab import userdata

HUGGING_FACE_TOKEN = userdata.get("HUGGING_FACE_TOKEN")
hf_dataset_name = "mrinjera/testing"

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

train_df, test_df = load_and_process_dataset("mrinjera/testing2", HUGGING_FACE_TOKEN)

train_split_df, val_split_df = create_validation_split(train_df)

val_queries, val_corpus, val_relevant_docs = create_evaluation_data(val_split_df)

test_queries, test_corpus, test_relevant_docs = create_evaluation_data(test_df)

Loading dataset: mrinjera/testing2
Train dataset loaded with 5 examples
Test dataset loaded with 5 examples
Dataset columns: ['function_name', 'docstring', 'question']
  Train: 5 examples
  Test: 5 examples
Created validation split:
  Training: 4 examples
  Validation: 1 examples
Created evaluation data with 1 queries and 1 documents
Created evaluation data with 5 queries and 5 documents


In [28]:
model = initialize_model(MODEL_NAME)

In [19]:
model

SentenceTransformer(
  (0): Transformer({'max_seq_length': 512, 'do_lower_case': False}) with Transformer model: RobertaModel 
  (1): Pooling({'word_embedding_dimension': 768, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': False, 'pooling_mode_max_tokens': True, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
)

In [29]:
train_model(model, train_split_df, val_queries, val_corpus, val_relevant_docs, device)

Computing widget examples:   0%|          | 0/1 [00:00<?, ?example/s]

<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize?ref=models
wandb: Paste an API key from your profile and hit enter:


Abort: 